In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

In [2]:
import numpy as np
import tensorflow as tf

In [3]:
## tensorflow logging enabled.
tf.logging.set_verbosity(tf.logging.INFO)

In [6]:
def cnn_model_fn(features, labels, mode):
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])
    conv1 = tf.layers.conv2d(inputs = input_layer, filters=32, kernel_size=[5,5], padding = "same", activation=tf.nn.relu)
    pool1 = tf.layers.max_pooling2d(inputs = conv1, pool_size=[2,2], strides = 2)
    conv2 = tf.layers.conv2d(inputs = pool1, filters=64, kernel_size=[5,5], padding="same", activation=tf.nn.relu)
    pool2 = tf.layers.max_pooling2d(inputs = conv2, pool_size=[2,2], strides = 2)
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(inputs = pool2_flat, units= 1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(inputs = dense, rate = 0.4, training= mode == tf.estimator.ModeKeys.TRAIN)
    logits = tf.layers.dense(inputs = dropout, units = 10)
    
    predictions = {
        "classes": tf.argmax(input = logits, axis=1),
        "probabilities" : tf.nn.softmax(logits, name = "softmax_tensor")
    }
    
    ## metrics for Train, Evaluate and Predict.
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode = mode, predictions = predictions)
    
    #calculate loss for both Train and evaluate metrics.
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)
    
    ## Training operators.
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate= 0.001)
        train_op = optimizer.minimize(loss= loss, global_step = tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode = mode, loss = loss, train_op= train_op)
    
    ## Evaluation metrics.
    eval_metrics_ops = {
        "accuracy": tf.metrics.accuracy(labels=labels, predictions=predictions["classes"])
    }
    
    return tf.estimator.EstimatorSpec(mode = mode, loss = loss, eval_metrics_ops = eval_metrics_ops)

In [10]:
def main(unused_argv):
    mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    train_data = mnist.train.images
    train_labels = np.asarray(mnist.train.labels, dtype = "int32")
    eval_data = mnist.test.images
    eval_labels = np.asarray(mnist.test.labels, dtype = "int32")
    
    
    ## Create an estimator.
    mnist_classifier = tf.estimator.Estimator(model_fn= cnn_model_fn, model_dir="C:/Users/lolla/Documents/Study/Research/Tensorflow_Practise/mnist_dump")
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)
    
    
    ## Train the model.
    train_input_fn = tf.estimator.inputs.numpy_input_fn(x = {"x" : train_data}, y = train_labels, batch_size = 100, num_epochs = None, shuffle = True)
    mnist_classifier.train(input_fn = train_input_fn, steps = 20000, hooks = [logging_hook])
    
    ## Evaluate a model.
  # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)

    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print(eval_results)  

In [11]:
if __name__ == "__main__":
    tf.app.run()

Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST-data\train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data\t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': 'C:/Users/lolla/Documents/Study/Research/Tensorflow_Practise/mnist_dump', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x000001CE372C2898>, '_task_type': 'worker', '_task_id':

INFO:tensorflow:loss = 2.31076, step = 1
INFO:tensorflow:probabilities = [[ 0.10326688  0.09861163  0.10222453  0.09652     0.10570674  0.10372943
   0.10333727  0.09507895  0.0849479   0.1065767 ]
 [ 0.09224235  0.11379646  0.09793603  0.10233664  0.09951264  0.10050964
   0.10001568  0.10197382  0.09751928  0.09415742]
 [ 0.10873321  0.09989256  0.10105283  0.10113513  0.09458631  0.09538563
   0.10005786  0.09774771  0.09984151  0.10156732]
 [ 0.12873271  0.10783093  0.0906049   0.10064107  0.08433481  0.09676038
   0.09028509  0.09075014  0.10494271  0.1051172 ]
 [ 0.10034432  0.10189451  0.10159674  0.09587997  0.09338965  0.09500802
   0.09648935  0.10322803  0.10485934  0.10731009]
 [ 0.1030557   0.09921978  0.10315854  0.09112585  0.10490263  0.10285342
   0.09994683  0.098861    0.0985835   0.09829283]
 [ 0.10739273  0.10396517  0.09091616  0.10359312  0.08914221  0.09725206
   0.10178749  0.09854586  0.11328591  0.09411926]
 [ 0.11069059  0.10554455  0.09116235  0.09866723  0

INFO:tensorflow:global_step/sec: 1.87098
INFO:tensorflow:probabilities = [[ 0.10114025  0.10394386  0.09248333  0.09239087  0.10024549  0.10205971
   0.09274414  0.10100702  0.11535085  0.09863447]
 [ 0.11439636  0.10633601  0.0999082   0.08799258  0.09272553  0.11360588
   0.08939018  0.09470945  0.10719644  0.0937394 ]
 [ 0.09927805  0.08207042  0.10237617  0.10602638  0.09676901  0.11022666
   0.10212634  0.1027919   0.10853573  0.08979935]
 [ 0.10340271  0.10689826  0.09458259  0.09094566  0.08957598  0.10162654
   0.0968302   0.09408171  0.11428076  0.10777561]
 [ 0.10137825  0.11613238  0.09131387  0.10635912  0.10458673  0.10240401
   0.09365905  0.09620971  0.09732366  0.09063319]
 [ 0.09624222  0.11120223  0.10028636  0.09225085  0.09379218  0.09507242
   0.08769652  0.10753518  0.11933288  0.09658916]
 [ 0.1033955   0.09047222  0.10154442  0.10078786  0.09765989  0.10536318
   0.10105683  0.09838276  0.11229252  0.08904476]
 [ 0.10665756  0.10125936  0.09677133  0.09387293  0

INFO:tensorflow:loss = 2.28682, step = 101 (53.427 sec)
INFO:tensorflow:probabilities = [[ 0.11912511  0.11049825  0.09555253  0.09131181  0.09217646  0.10734079
   0.09884275  0.09140538  0.09125338  0.10249349]
 [ 0.09920593  0.09953432  0.09387323  0.1047481   0.09607274  0.09794046
   0.09397105  0.08764122  0.11651787  0.11049514]
 [ 0.10174527  0.09163599  0.09734932  0.09975328  0.09781677  0.11446935
   0.10815155  0.09789478  0.09197875  0.09920495]
 [ 0.09653292  0.10441087  0.10757605  0.10376263  0.09778993  0.1013109
   0.09288291  0.10117886  0.10122772  0.09332722]
 [ 0.10150439  0.09496437  0.10071906  0.10461979  0.09580047  0.1052198
   0.09837827  0.09419087  0.10138458  0.10321839]
 [ 0.10797124  0.10653844  0.09485732  0.10016911  0.09631252  0.10644001
   0.09676522  0.08266892  0.10533883  0.10293842]
 [ 0.10590277  0.10374154  0.09749286  0.09463982  0.10457963  0.09976067
   0.10080118  0.09692109  0.10022575  0.09593478]
 [ 0.09342711  0.09669825  0.09070355  

INFO:tensorflow:global_step/sec: 1.85621
INFO:tensorflow:probabilities = [[ 0.11104471  0.09359825  0.09685143  0.10372909  0.09128885  0.09542113
   0.10062544  0.09949923  0.1039231   0.10401887]
 [ 0.10865001  0.08905505  0.11325216  0.10194141  0.11067676  0.09863177
   0.08918238  0.09434009  0.10825927  0.08601107]
 [ 0.09668332  0.09901419  0.09914632  0.0935372   0.09939742  0.1016104
   0.10914614  0.09320687  0.1078889   0.10036933]
 [ 0.09765147  0.11049818  0.10728858  0.0961237   0.09692704  0.09135776
   0.1022443   0.1036436   0.09614114  0.09812419]
 [ 0.1111951   0.096096    0.09873745  0.10145649  0.09900234  0.08891068
   0.10574505  0.08951626  0.11789744  0.09144326]
 [ 0.09912919  0.1050898   0.09316919  0.10617837  0.09173509  0.09523277
   0.09889475  0.09730532  0.10326868  0.10999686]
 [ 0.09570193  0.09695403  0.10052976  0.09153383  0.08684309  0.10999697
   0.11492675  0.1069076   0.1005878   0.09601831]
 [ 0.09491012  0.10902356  0.09780005  0.10176928  0.

...

INFO:tensorflow:global_step/sec: 2.92324
INFO:tensorflow:probabilities = [[ 0.0547164   0.00026952  0.01088743  0.01638099  0.00003914  0.00388905
   0.9131915   0.00043088  0.00019271  0.00000234]
 [ 0.0000042   0.0000008   0.00000117  0.00008863  0.00194177  0.00008926
   0.00000025  0.14113668  0.00037955  0.85635775]
 [ 0.00000021  0.00000001  0.00000002  0.00001298  0.00000009  0.00000033
   0.          0.99995828  0.00000036  0.00002783]
 [ 0.98934454  0.00001231  0.00089376  0.00034692  0.0000021   0.00344106
   0.00051272  0.00322635  0.00002085  0.00219935]
 [ 0.00000073  0.00027531  0.00156589  0.00036328  0.0000006   0.00001003
   0.00000009  0.99773979  0.0000178   0.00002639]
 [ 0.00008109  0.00002535  0.00147375  0.0000918   0.00004964  0.00024698
   0.9958396   0.00000504  0.0021834   0.00000342]
 [ 0.99669647  0.00000115  0.00021242  0.00000114  0.00000004  0.00181217
   0.00123188  0.00000044  0.00004303  0.00000121]
 [ 0.00000131  0.99878734  0.00018079  0.00057336  0

INFO:tensorflow:loss = 0.0570957, step = 14501 (34.205 sec)
INFO:tensorflow:probabilities = [[ 0.00000267  0.99804568  0.00113355  0.00015123  0.00001322  0.00000059
   0.00000559  0.00054336  0.00010099  0.00000312]
 [ 0.00023433  0.00001878  0.00001214  0.0003681   0.00418761  0.00057349
   0.00000745  0.01772672  0.00087526  0.9759962 ]
 [ 0.00000204  0.0000002   0.0000013   0.00245565  0.0000575   0.00017312
   0.          0.03884668  0.00002926  0.95843428]
 [ 0.99686939  0.00000522  0.00275473  0.00015001  0.0000013   0.00002868
   0.00002211  0.00003003  0.00000471  0.00013385]
 [ 0.00000062  0.00020791  0.00004134  0.00550571  0.9789027   0.0002613
   0.00001472  0.00032707  0.00228677  0.01245191]
 [ 0.00001623  0.00000134  0.00023149  0.00000057  0.9957267   0.00001182
   0.00291434  0.00002073  0.00007691  0.0009998 ]
 [ 0.00007354  0.00059712  0.12160773  0.02495074  0.00024131  0.03357701
   0.00040667  0.00000107  0.81846648  0.00007836]
 [ 0.00005078  0.02852665  0.10524

INFO:tensorflow:global_step/sec: 2.90154
INFO:tensorflow:probabilities = [[ 0.00002716  0.00001574  0.00011239  0.00057721  0.00001541  0.00008983
   0.00000001  0.97767055  0.00043618  0.02105543]
 [ 0.00000534  0.00000098  0.00003169  0.00003141  0.01634743  0.00000383
   0.00000055  0.00015557  0.0001348   0.98328835]
 [ 0.00000743  0.00000161  0.00000252  0.00001285  0.00000143  0.99977762
   0.00000128  0.00000085  0.00019348  0.00000093]
 [ 0.00000135  0.00000709  0.00000577  0.00022116  0.80734086  0.00126645
   0.00000124  0.00448373  0.00183304  0.18483926]
 [ 0.00000091  0.00000003  0.00000317  0.          0.00000225  0.0000001
   0.99999213  0.          0.00000138  0.00000002]
 [ 0.00012974  0.00054562  0.15906845  0.03834071  0.00001369  0.00000289
   0.00000083  0.77279443  0.0001078   0.02899586]
 [ 0.00001126  0.00001245  0.0000238   0.99409986  0.00000303  0.00575017
   0.00004415  0.00000035  0.00004305  0.00001182]
 [ 0.20412979  0.00011526  0.00194997  0.57584125  0.

INFO:tensorflow:loss = 0.124851, step = 14601 (34.461 sec)
INFO:tensorflow:probabilities = [[ 0.00003834  0.00001067  0.00255449  0.94029081  0.00000969  0.03752111
   0.00000344  0.00000029  0.01952643  0.00004456]
 [ 0.00000995  0.00011556  0.9805572   0.01539528  0.00012366  0.00001455
   0.00000515  0.00126995  0.00088032  0.00162843]
 [ 0.00697558  0.00003273  0.00025439  0.00001317  0.00015578  0.00124181
   0.00002016  0.00054357  0.99028641  0.00047649]
 [ 0.00000678  0.99728     0.00007199  0.00162599  0.00008398  0.00008098
   0.00001926  0.00016304  0.00044218  0.00022585]
 [ 0.00001793  0.00041337  0.00515259  0.00784809  0.88404059  0.00118247
   0.00049066  0.00012616  0.00089558  0.09983265]
 [ 0.98267394  0.00000699  0.00059368  0.00063781  0.00000736  0.01365724
   0.00072628  0.0007271   0.00022271  0.00074678]
 [ 0.00058668  0.00000148  0.00007698  0.0000021   0.00039488  0.00157389
   0.99723238  0.00000103  0.00001076  0.00011974]
 [ 0.00000049  0.00004159  0.00009

KeyboardInterrupt: 